# Get McDonald's locations

#### Load Python tools and Jupyter config

In [1]:
import us
import json
import requests
import pandas as pd
import jupyter_black
import altair as alt
import geopandas as gpd
from bs4 import BeautifulSoup
from vega_datasets import data as vega_data
from tqdm.notebook import tqdm, trange

In [2]:
jupyter_black.load()
pd.options.display.max_columns = 100
pd.options.display.max_rows = 1000
pd.options.display.max_colwidth = None
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [3]:
place = "mcdonalds"
place_formal = "McDonald's"
color = "#d90007"
today = pd.Timestamp.today().strftime("%Y-%m-%d")

---

## Scrape

In [4]:
zips_all = pd.read_json(
    "../../_reference/data/zips_reference_pop_gen.json"
).sort_values("population", ascending=False)

In [5]:
zips_all["zip"] = zips_all["zip"].astype(str).str.zfill(5).to_list()

#### Get the most populous ZIPs and a sample of the rest

In [6]:
# zips_top = zips_all.head(1000)
# zips_sample = zips_all.tail(len(zips_all) - 1000).sample(1000)
# zips_df = (
#     pd.concat([zips_sample, zips_top])
#     .reset_index(drop=True)
#     .sort_values("population", ascending=False)
# )

#### Headers for request

In [7]:
headers = {
    "authority": "www.mcdonalds.com",
    "user-agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/122.0.0.0 Safari/537.36",
}

In [8]:
extracted_info = []

for index, row in tqdm(zips_all.iterrows(), total=zips_all.shape[0]):
    longitude = row["longitude"]
    latitude = row["latitude"]

    params = {
        "latitude": latitude,
        "longitude": longitude,
        "radius": "20",
        "maxResults": "100",
        "country": "us",
        "language": "en-us",
    }

    try:
        response = requests.get(
            "https://www.mcdonalds.com/googleappsv2/geolocation",
            params=params,
            headers=headers,
        )

        locations = response.json()["features"]

        for location in locations:
            location_number = location["properties"]["identifierValue"]
            location_name = location["properties"]["shortDescription"]
            street = location["properties"]["addressLine1"]
            city = location["properties"]["addressLine3"]
            state = location["properties"]["subDivision"]
            zipcode = location["properties"]["postcode"]
            longitude = location["geometry"]["coordinates"][0]
            latitude = location["geometry"]["coordinates"][1]
            street = location["properties"]["addressLine1"]
            # phone = location["properties"]["telephone"]
            # timezone = location["properties"]["timeZone"]

            location_info = {
                "store_number": location_number,
                "store_name": location_name,
                "street": street,
                "city": city,
                "state": state,
                "zip": zipcode,
                # "phone": phone,
                "latitude": latitude,
                "longitude": longitude,
                # "timezone": timezone,
            }
            extracted_info.append(location_info)

    except requests.exceptions.HTTPError as err:
        print(f"HTTP Error for {latitude}, {longitude}: {err}")
    except Exception as e:
        print(f"HTTP Error for {latitude}, {longitude}: {e}")

  0%|          | 0/6063 [00:00<?, ?it/s]

#### Into a dataframe

In [9]:
df = pd.DataFrame(extracted_info).drop_duplicates()

#### How many locations?

In [10]:
len(df)

11197

#### The result:

In [11]:
df.head()

store_number        store_name                  street  city state    zip  \
0        32631  FM 1093 AT GREEN   25647 Westheimer Pkwy  Katy    TX  77494   
1        34885  CINCO RANCH AT S  27140 Cinco Ranch Blvd  Katy    TX  77494   
2        35856     I-10 AND 1463      26149 Katy Freeway  Katy    TX  77494   
3        13012       KATY-HWY 90             5701 Hwy 90  Katy    TX  77494   
4        33124  FRY AT GRAND PKW           7104 S Fry Rd  Katy    TX  77494   

    latitude  longitude  
0  29.749788 -95.798871  
1  29.715545 -95.813882  
2  29.776382 -95.831192  
3  29.785563 -95.822533  
4  29.716436 -95.778050

#### Create a mapping of state abbreviations to full state names using the us library

In [12]:
state_mapping = {state.abbr: state.name for state in us.states.STATES}

#### New column of full state names based on abbreviations

In [13]:
df["state_name"] = df["state"].map(state_mapping)

#### Make sure our brand name gets in the dataframe

In [14]:
df["brand"] = place_formal

#### Add fetch date

In [15]:
df["updated"] = today

---

## Geography

#### Make it a geodataframe

In [16]:
df_geo = df.copy()

In [17]:
gdf = gpd.GeoDataFrame(
    df_geo, geometry=gpd.points_from_xy(df_geo.longitude, df_geo.latitude)
).set_crs("4326")

---

## Maps

#### US states background

In [18]:
background = (
    alt.Chart(alt.topo_feature(vega_data.us_10m.url, feature="states"))
    .mark_geoshape(fill="#e9e9e9", stroke="white")
    .properties(width=800, height=500, title=f"{place_formal} locations")
    .project("albersUsa")
)

#### Location points map

In [19]:
points = (
    alt.Chart(gdf)
    .mark_circle(size=5, color=color)
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
    )
)

point_map = background + points
point_map.configure_view(stroke=None)

alt.LayerChart(...)

#### Location proportional symbols map

In [20]:
symbols = (
    alt.Chart(gdf)
    .transform_aggregate(
        latitude="mean(latitude)",
        longitude="mean(longitude)",
        count="count()",
        groupby=["state"],
    )
    .mark_circle()
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
        size=alt.Size("count:Q", title="Count by state"),
        color=alt.value(color),
        tooltip=["state:N", "count:Q"],
    )
    .properties(
        title=f"Number of {place_formal} in US, by average lon/lat of locations"
    )
)

symbol_map = background + symbols
symbol_map.configure_view(stroke=None)

alt.LayerChart(...)

---

## Exports

#### JSON

In [21]:
df.to_json(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.json",
    indent=4,
    orient="records",
)

#### CSV

In [22]:
df.to_csv(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.csv", index=False
)

#### GeoJSON

In [23]:
gdf.to_file(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.geojson",
    driver="GeoJSON",
)